# Lesson 7. Comparing alternate systems

### SA421 Fall 2015

## The problem: simulating a change to a system

* You have been asked by Transport for London to study the feasibility of replacing the manned ticket offices with automated ticket machines in its underground stations. ([Actually, it already has decided to do so.](http://www.standard.co.uk/news/transport/hundreds-of-tube-ticket-offices-to-shut-as-machines-replace-staff-8883895.html))


* You have decided to focus on the evening rush hour period, from 16:00 to 20:00, at a very small station with 1 employee at the ticket office, which will be replaced by 1 machine.


* Using historical data that has been provided to you, you have determined that the time between customers arrivals at the ticket office/machine is exponentially distributed with a mean of 3.2 minutes. 


* In addition, you have determined using this data that the service time (in minutes) at the manned ticket office can be modeled with a Gamma random variable with shape parameter 2 and scale parameter 1.3. 


* Through its own studies, Transport for London has determined that the service time (in minutes) at the automated ticket machine can be modeled with a Gamma random variable with shape parameter 1 and scale parameter 2.6.

What is the effect of this transition to automated ticketed machines on the average delay that a customer experiences?

* First, as usual, some setup code.


* What's new/different:
    - `gamma` from `numpy.random`
    - `levene` and `ttest_ind` from `scipy.stats`

In [ ]:
##### Setup #####
# Import everything from SimPy
from SimPy.Simulation import *

# Import mean, std, sqrt functions from NumPy
from numpy import mean, std, sqrt

# Import seed initializer and random sampling functions from NumPy
from numpy.random import seed, exponential, gamma

# Import t random variable from scipy.stats
from scipy.stats import t, levene, ttest_ind

* Below is a SimPy simulation model, very similar to the one for the Fantastic Dan problem, with a monitor set up for customer delay.


* Note that the service time parameters have been initialized to `None`. We will fill them in later, before running the model.

In [ ]:
##### Parameters #####
class P:
    # Customers arrive at the ticket office/machine with 
    # exponentially distributed interarrival times with mean 3.2
    interarrivalTimeMean = 3.2
    
    # Service times follow gamma distribution with some shape/scale parameters
    serviceTimeShape = None
    serviceTimeScale = None
    
    # One server: we assume there is 1 employee or 1 machine
    nServers = 1
    
    # Simulation time: 4 hours
    simulationTimeMax =  4 * 60
    

##### Processes #####
# Customer
class Customer(Process):
    def behavior(self):
        # Customer arrives, joins queue
        # Record customer arrival time
        arrivalTime = now()
        yield request, self, R.server
        
        # Customer is released from queue and starts service
        # Observe customer delay using monitor
        M.delay.observe(now() - arrivalTime)
        serviceTime = gamma(shape = P.serviceTimeShape, scale = P.serviceTimeScale)
        yield hold, self, serviceTime
        
        # Customer finishes service, leaves
        yield release, self, R.server

# Entrance
class Entrance(Process):
    def behavior(self):
        # At the start of the simulation, no customers have arrived
        nCustomers = 0
        
        # Customer arrivals
        while True:
            # Wait until the next arrival
            interarrivalTime = exponential(scale = P.interarrivalTimeMean)
            yield hold, self, interarrivalTime
            
            # Create a new customer using the template defined in the Customer class
            c = Customer(name="Customer {0}".format(nCustomers))
            
            # Activate the customer's behavior
            activate(c, c.behavior())

            # Count this new customer
            nCustomers += 1

            
##### Resources #####
class R:
    # Server
    server = None
    
    
##### Monitors #####
class M:
    # Delay
    delay = None


##### Model #####
def model(inputSeed):
    # Initialize SimPy 
    initialize()

    # Initialize a seed for the random number generator
    seed(inputSeed)

    # Create the server resource
    R.server = Resource(capacity = P.nServers)
    
    # Create the monitor for customer delay
    M.delay = Monitor()

    # Activate the entrance (to generate customers)
    e = Entrance()
    activate(e, e.behavior())
    
    # Run the simulation
    simulate(until = P.simulationTimeMax)

    # Compute performance measure: average delay
    avgDelay = M.delay.mean()
    
    # Return performance measure
    return avgDelay

* Let's run the simulation model 100 times for two alternate systems.


* First, the current system with the manned ticket office (System 1):

In [ ]:
##### Experiment - System 1 #####
P.serviceTimeShape = 2
P.serviceTimeScale = 1.3

# Number of observations

# Collect observations of average delay into avgDelay1Obs


* Next, the proposed system with the automated ticket machine (System 2):

In [ ]:
##### Experiment - System 2 #####
P.serviceTimeShape = 1
P.serviceTimeScale = 2.6

# Number of observations

# Collect observations of average delay into avgDelay2Obs


* For both systems, let's compute the observed sample mean of average delay, the observed standard deviation and confidence intervals for the mean.

In [ ]:
##### System 1 #####
# Observed sample mean
avgDelay1SM = 

# Observed sample standard deviation
avgDelay1SSD = 

# Confidence level 0.05
alpha = 0.05
avgDelay1CIL = 
avgDelay1CIR = 

print("SYSTEM 1")
print("Average delay:")
print("  Sample mean: {0}".format(avgDelay1SM))
print("  Sample standard deviation: {0}".format(avgDelay1SSD))
print("  {0}% confidence interval: [{1}, {2}]".format((1 - alpha)*100, avgDelay1CIL, avgDelay1CIR))

In [ ]:
##### System 2 #####
# Observed sample mean
avgDelay2SM = 

# Observed sample standard deviation
avgDelay2SSD = 

# Confidence level 0.05
alpha = 0.05
avgDelay2CIL = 
avgDelay2CIR = 

print("SYSTEM 2")
print("Average delay:")
print("  Sample mean: {0}".format(avgDelay2SM))
print("  Sample standard deviation: {0}".format(avgDelay2SSD))
print("  {0}% confidence interval: [{1}, {2}]".format((1 - alpha)*100, avgDelay2CIL, avgDelay2CIR))

* The observed sample means of the average delay for the two systems are different, but not by much.


* How do we know this difference is not just an artifact of simulation?


* Can we <span style="color:#a00000;">statistically prove</span> that these average delay estimates are the same or different?

## Testing for equal means

* We can use a **$t$-test for equal means** to test if the mean average delay in the 2 systems are in fact statistically different. 


* How we perform the $t$-test differs, depending on whether the variance of the average delay in the 2 systems are different. 


* Looking at the sample standard deviations, it's not immediately clear if the variance of the average delay is different across these 2 systems.


* So, before we perform the $t$-test for equal means, we can perform the **Levene test for equal variances** to test whether the variances are equal.

### Levene test for equal variances

* Let $X_1,\dots,X_m$ be identically distributed random variables with unknown mean $\mu_X$ and variance $\sigma^2_X$.


* Let $Y_1,\dots,Y_n$ be identically distributed random variables with unknown mean $\mu_Y$ and variance $\sigma^2_Y$.


* Null hypothesis $H_0$: $\sigma^2_X = \sigma^2_Y$.


* $p$-value: 
$$\Pr\{ \text{Test statistic} \ge \text{Observed test statistic} \;|\; H_0 \text{ is true}\}$$



* Let's set a significance level of $\alpha = 0.05$.


* If $p$-value is low (i.e., less than $\alpha$), then we reject the null hypothesis.


* Otherwise, we do not reject the null hypothesis.


* To perform the Levene test, we can use `levene` from `scipy.stats`:

In [ ]:
# Perform Levene test

# Print p-value of Levene test


*Write your conclusions from the Levene test here. Double-click to edit.*

### $t$-test for equal means

* Again, let $X_1,\dots,X_m$ be identically distributed random variables with unknown mean $\mu_X$ and variance $\sigma^2_X$.


* Also, let $Y_1,\dots,Y_n$ be identically distributed random variables with unknown mean $\mu_Y$ and variance $\sigma^2_Y$.


* $p$-value: 
$$\Pr\{ \text{Test statistic} \ge \text{Observed test statistic} \;|\; H_0 \text{ is true}\}$$


* Null hypothesis $H_0$: $\mu_X = \mu_Y$.


* To perform the $t$-test, we can use `ttest_ind` from `scipy.stats`:

In [ ]:
# Perform t-test with equal variances

# Print p-value of t-test


*Write your conclusions from the t-test here. Double-click to edit.*

* If the variances had not been equal, we would need to set `equal_var` to `False` when calling `ttest_ind`.

## Discussion

* Do you think our approach and the resulting conclusion is valid? Why or why not? What changes would you make, if any? 

*Write your notes here. Double-click to edit.*